In [1]:
from __future__ import division, print_function
import os
import numpy as np
import time
import copy

# equivalences:
# Python 2       Python 3
# -----------------------
# range(4)       list(range(4))
# xrange(4)      range(4)
try:
    range = xrange  # fails in Python 3
except:
    Pass


    
# reading in knapsack instance:
numOfItems = 10
instanceNumber = 1
filename = 'C://users/dimo/desktop/teaching/Saclay2015/introToOptimization/02-dynProgAndBranchBound/knapsackinstances/KP-random-%ditems-%d.txt' % (numOfItems, instanceNumber)
w = []
p = []
with open(filename, "r") as text_file:
        for line in text_file:
            ll = line.split()
            if 'W' in ll[0]:
                W = int(ll[2])
            if 'n' not in ll[0] and 'W' not in ll[0]:
                w.append(int(ll[0]))
                p.append(int(ll[1]))
                


In [2]:
# alternative: using urllib2 module
import urllib2
file = urllib2.urlopen('http://researchers.lille.inria.fr/~brockhof/introoptimization/knapsackinstances/KP-random-%ditems-%d.txt' % (numOfItems, instanceNumber))
data = file.readlines()
n = int((data[0].split(' '))[2])
W = int((data[1].split(' '))[2])
w = []
p = []
for i in range(2,len(data)):
    w.append(int((data[i].split(' '))[0]))
    p.append(int((data[i].split(' '))[1]))


In [3]:
# first ensure that items are stored in increasing order of their
# profit/weight ratio which makes it easier to write down the
# greedy algorithm:
w = np.array(w)
p = np.array(p)
profweightratio = np.array(p) / np.array(w)
idx = np.argsort(profweightratio)
w = w[idx]
p = p[idx]

In [4]:
# defining the problem's objective and constraint functions, both
# available for a single or parallel evaluation of multiple solutions

def f(x):   # objective function
    if (len(x.shape)==1):
        return np.sum(p*x)
    else:
        return np.sum(p*x, axis=1)

def g(x):   # constraint function violation
    if (len(x.shape)==1):
        return np.sum(w*x) - W
    else:
        return np.sum(w*x, axis=1) - np.tile(W, x.shape[0])

In [5]:
def optimizegreedy(p, w):
    '''
    Implements a simple greedy algorithm for the knapsack problem.
    
    Computes a solution greedily by adding items with highest
    profit/weight ratio iteratively until the solution is infeasible.

    '''
    sol = np.zeros(len(w))
    for i in reversed(range(len(w))):
        sol[i] = 1
        if g(sol)>0:
            sol[i] = 0
            break
    return sol

In [6]:
def optimizeinversegreedy(p, w):
    '''
    Implements an inversed greedy algorithm for the knapsack
    problem.
    
    Computes a solution greedily by removing items with lowest
    profit/weight ratio iteratively until the solution is feasible.

    '''
    sol = np.ones(len(w))
    for i in range(len(w)):
        sol[i] = 0
        if g(sol)<=0:
            break
    return sol

In [7]:
# brute-force algorithm:

def optimizebruteforce(f, g, n):
    '''
    Implements a brute force algorithm (aka a full enumeration of
    the search space) to compute the optimum of the binary problem
              max f: {0,1}^n --> R
              s.t. g(x) <= 0

    notations/prerequisites:
    f: objective function
    g: constraint violation (g(x) negative --> x feasible)
    n: problem dimension (= #(binary variables))
    
    '''
    
    f_bestsofar = -np.infty
    solution_bestsofar = []

    # create and evaluate all bitstrings of length n
    for i in xrange(0,2**n):
        # conversion from integer to binary representation as numpy array:
        x = np.array([int(j) for j in np.binary_repr(i, n)])

        # if new solution better than best so far & feasible, keep it:
        if f(x) > f_bestsofar and g(x) <= 0:
            f_bestsofar = f(x)
            solution_bestsofar = x

    return (solution_bestsofar, f_bestsofar)

In [8]:
tic = time.time()
solgreedy = optimizegreedy(p, w)
print("greedy solution with f=%d:" % f(solgreedy))
print(solgreedy)
toc = time.time()
t_greedy = toc - tic
print('%e sec elapsed' % (toc - tic))

tic = time.time()
solinvgreedy = optimizeinversegreedy(p, w)
print("inverse greedy solution with f=%d:" % f(solinvgreedy))
print(solinvgreedy)
toc = time.time()
t_invgreedy = toc - tic
print('%e sec elapsed' % (toc - tic))

tic = time.time()
bruteforceBestX, brutforceBestF = optimizebruteforce(f, g, numOfItems)
print("brute force: optimal solution with f=%d:" % f(bruteforceBestX))
print(bruteforceBestX)
toc = time.time()
t_bruteforce = toc - tic
print('%e sec elapsed' % (toc - tic))

greedy solution with f=298:
[ 0.  0.  0.  0.  0.  1.  1.  1.  1.  1.]
9.999275e-04 sec elapsed
inverse greedy solution with f=298:
[ 0.  0.  0.  0.  0.  1.  1.  1.  1.  1.]
0.000000e+00 sec elapsed
brute force: optimal solution with f=308:
[0 0 1 0 1 0 1 1 1 1]
1.500010e-02 sec elapsed


In [31]:
# results:
#
#                    n=10                     n=20                     n=30
# instance    1       2       3        1       2       3        1       2       3
# -----------------------------------------------------------------------------------
# exact f    308     322     333      740     662     686    >=1026* >=1001* >=933*
# time     1.8e-2s 2.2e-2s 2.3e-2s    22s     21s     21s      ~7h*    ~7h*   ~7h* 
# -----------------------------------------------------------------------------------
# greedy     298     309     333      728     643     650      1001    967     923
# time     1.0e-3s 2.0e-3s 1.0e-3s  1.0e-3s 2.0e-3s 1.0e-3s  2.0e-3s 3.0e-3s 1.0e-3s
#
# *the exact algorithm has not been run until the end and thus only a lower bound on
#  the optimal function value and an estimate of its runtime can be given.

In [6]:
# optional: brute force, recursive algorithm

# returns all bitstrings of length n in list s
def getAllBitstrings(n):
    if (n == 1):
        s = [[0],[1]]
    else:
        tmp = getAllBitstrings(n-1)
        s = []
        for t in tmp:
            s1 = copy.deepcopy(t)
            s1.append(0)
            s2 = copy.deepcopy(t)
            s2.append(1)
            s.append(s1)
            s.append(s2)
    return s

# evaluates each bit string in search space
def optimizebruteforcerecursive():
    bestsofarf = -np.infty
    bestsofarsolution = []

    for solution in getAllBitstrings(numOfItems):
        # create numpy array from the list:
        x = np.array(solution)

        # if new solution is better than best so far and feasible, keep it
        if f(x) > bestsofarf and g(x) <= 0:
            bestsofarf = f(x)
            bestsofarsolution = x

    return bestsofarsolution

In [7]:
tic = time.time()
bruteforcerecursive = optimizebruteforcerecursive()
print("brute force: optimal solution with f=%d:" % f(bruteforcerecursive))
print(bruteforcerecursive)
toc = time.time()
t_bruteforcerecursive = toc - tic
print('%e sec elapsed' % (toc - tic))

brute force: optimal solution with f=333:
[0 0 0 0 0 1 1 1 1 1]
4.600000e-02 sec elapsed
